# Overview

**GENERAL THOUGHTS:**  
Use AutoML (AutoGluon.Tabular) as a general way to investigate which algorithm, pre-processing, feature engineering options are (well) suited for the given tasks, as well as to investigate the potential performance based on a (large) varity of configurations of those options.
The notebook includes multiple scenarios of using AutoML:
- including and excluding custom data pre-processing (see below)
- including auto pre-processing by AutoGluon.Tabular
- including auto feature engineering by AutoGluon.Tabular
https://auto.gluon.ai/stable/tutorials/tabular/tabular-feature-engineering.html
- including multiple classifiers by using:
  - multiple ml algorithms
  - "standard" HPO for each algorithm defined by AutoGluon.Tabular
  - ensables of algorithms (bagging and stacking with possible multiple layers)

**CUSTOM DATA PREPROCESSING:**

Imbalanced data:
- over_sampling for imbalanced data
- cost-sensitive learning for imbalanced data

numeric data:
- data imputation: SimpleImputer(strategy='median')
- data scaling: PowerTransformer() using 'log_transform'

categorical data:
- data imputation: SimpleImputer(strategy='most_frequent')
- categorical data encoding: OrdinalEncoder(handle_unknown='use_encoded_value', unknown_value=np.nan)

**AUTOML MULTI-CLASS CLASSIFIERS:**
- Overview of models to be considered using AutoML (AutoGluon.Tabular):  
  - [X] RandomForest
  - [X] ExtraTrees
  - [X] XGBoost
  - [X] LightGBM
  - [X] KNeighbors
  - [X] CatBoost

In [ ]:
import numpy as np
import pandas as pd
import matplotlib.pyplot as plt
import seaborn as sns

import mlflow

import os
from datetime import datetime

In [ ]:
import sklearn
from sklearn.pipeline import Pipeline
from sklearn.compose import ColumnTransformer
from sklearn.model_selection import train_test_split
from sklearn.impute import SimpleImputer
from sklearn.preprocessing import LabelEncoder, OrdinalEncoder, OneHotEncoder, MinMaxScaler, StandardScaler
from sklearn.preprocessing import PowerTransformer
from sklearn.metrics import classification_report

import imblearn
from imblearn.over_sampling import RandomOverSampler

from autogluon.tabular import TabularDataset, TabularPredictor

import yaml
with open('../env_vars.yml', 'r') as file:
        config = yaml.safe_load(file)

import warnings
# Ignore specific warnings by category
warnings.filterwarnings("ignore", category=FutureWarning)

In [3]:
# General settings within the data science workflow

pd.set_option('display.max_columns', None)

SEED = 42

# NOTE: for dev only
subsample = False
subsample_size = 100  # subsample subset of data for faster demo or development


# Get current date and time
now = datetime.now()
# Format date and time
formatted_date_time = now.strftime("%Y-%m-%d_%H:%M:%S")
print(formatted_date_time)

2024-04-04_10:30:04


# Load and prepare data

In [ ]:
df = pd.read_csv(f"{config['data_directory']}/output/df_ml.csv", sep='\t')

df['material_number'] = df['material_number'].astype('object')

df_sub = df[[
    'material_number',
    'brand',
    'product_area',
    'core_segment',
    'component',
    'manufactoring_location',
    'characteristic_value',
    'material_weight', 
    'packaging_code',
    'packaging_category',
]]

# AutoML: without custom pre-processing; restricted selection of models including HPO and model ensembling

## Split data into train and test

In [5]:
# Define features and target
X = df_sub.iloc[:, :-1]
y = df_sub.iloc[:, -1]  # the last column is the target

In [6]:
# Generate train/test sets
X_train, X_test, y_train, y_test = train_test_split(
    X, y, test_size=0.2, stratify=y,
    random_state=SEED
)

## Transform to AutoML data format

In [7]:
df_train = pd.concat([X_train, y_train], axis=1)

In [8]:
train_data = TabularDataset(df_train)
if subsample is True:
    train_data = train_data.sample(n=subsample_size, random_state=SEED)

## AutoML training pipeline

In [9]:
label = 'packaging_category'
automl_predictor = TabularPredictor(
    label=label,
    problem_type='multiclass',
    eval_metric='f1_macro',
    sample_weight='balance_weight'
).fit(
    train_data=train_data,
    tuning_data=None, # If tuning_data = None, fit() will automatically hold out some random validation examples from train_data.
    holdout_frac=0.2, # Default value (if None) is selected based on the number of rows in the training data.
    time_limit=3*60*60,
    presets=['best_quality'], # default = ['medium_quality'], any user-specified arguments in fit() will override the values used by presets.
    # auto_stack=False, # Whether AutoGluon should automatically utilize bagging and multi-layer stack ensembling to boost predictive accuracy.
    # included_model_types=['LR', 'KNN', 'RF', 'XT', 'GBM', 'XGB', 'CAT', 'NN'],
    # excluded_model_types=['FASTAI', 'AG_AUTOMM'],
    hyperparameter_tune_kwargs = {  # HPO is not performed unless hyperparameter_tune_kwargs is specified. Searchspaces are provided for some models, but not for all. Where no searchspace is provided, a fixed set of hyper-parameters is defined. (see /searchspace under each model: https://github.com/autogluon/autogluon/tree/master/tabular/src/autogluon/tabular/models).
        # 'num_trials': 15, # try at most n different hyperparameter configurations for each type of model
        'scheduler' : 'local',
        'searcher': 'auto', # ‘auto’: Perform bayesian optimization search on NN_TORCH and FASTAI models. Perform random search on other models.
    }  # Refer to TabularPredictor.fit docstring for all valid values
)

No path specified. Models will be saved in: "AutogluonModels/ag-20240404_083007"
Presets specified: ['best_quality']
Stack configuration (auto_stack=True): num_stack_levels=1, num_bag_folds=8, num_bag_sets=1
Dynamic stacking is enabled (dynamic_stacking=True). AutoGluon will try to determine whether the input data is affected by stacked overfitting and enable or disable stacking as a consequence.
Detecting stacked overfitting by sub-fitting AutoGluon on the input data. That is, copies of AutoGluon will be sub-fit on subset(s) of the data. Then, the holdout validation data is used to detect stacked overfitting.
Sub-fit(s) time limit is: 10800 seconds.
Starting holdout-based sub-fit for dynamic stacking. Context path is: AutogluonModels/ag-20240404_083007/ds_sub_fit/sub_fit_ho.
Using predefined sample weighting strategy: balance_weight. Evaluation metrics will ignore sample weights, specify weight_evaluation=True to instead report weighted metrics.
Beginning AutoGluon training ... Time l

In [10]:
# Evaluation of models on training data
automl_predictor.leaderboard()

model  score_val eval_metric  pred_time_val  \
0           WeightedEnsemble_L2   0.834099    f1_macro       0.177090   
1           XGBoost_r194_BAG_L1   0.813718    f1_macro       0.002539   
2       RandomForest_r16_BAG_L1   0.729467    f1_macro       0.004541   
3      RandomForest_r195_BAG_L1   0.713571    f1_macro       0.005491   
4        ExtraTrees_r197_BAG_L1   0.708666    f1_macro       0.003758   
..                          ...        ...         ...            ...   
71        KNeighborsUnif_BAG_L1   0.259520    f1_macro       0.004361   
72          CatBoost_r60_BAG_L1   0.258506    f1_macro       0.003954   
73          CatBoost_r69_BAG_L1   0.252697    f1_macro       0.003968   
74         CatBoost_r137_BAG_L1   0.238069    f1_macro       0.003943   
75  NeuralNetFastAI_r100_BAG_L1   0.176119    f1_macro       0.003949   

      fit_time  pred_time_val_marginal  fit_time_marginal  stack_level  \
0   310.831368                0.030227          81.133102            2   
1    55.940349                0.002539          55.940349            1   
2     7.771133                0.004541           7.771133            1   
3     6.863560                0.005491           6.863560            1   
4     4.498879                0.003758           4.498879            1   
..         ...                     ...                ...          ...   
71    0.344967                0.004361           0.344967            1   
72   49.744486                0.003954          49.744486            1   
73   47.963369                0.003968          47.963369            1   
74   50.568233                0.003943          50.568233            1   
75   52.304650                0.003949          52.304650            1   

    can_infer  fit_order  
0        True         76  
1        True         22  
2        True         65  
3        True         17  
4        True         63  
..        ...        ...  
71       True          1  
72       True         55  
73       True         24  
74       True         14  
75       True         69  

[76 rows x 10 columns]

In [11]:
# Evaluation of models on test data
df_test = pd.concat([X_test, y_test], axis=1)
test_data = TabularDataset(df_test)

automl_std_leaderboard_testdata = automl_predictor.leaderboard(test_data)
automl_std_leaderboard_testdata.head(10)

model  score_test  score_val eval_metric  \
0       WeightedEnsemble_L2    0.770424   0.834099    f1_macro   
1       XGBoost_r194_BAG_L1    0.763045   0.813718    f1_macro   
2   RandomForest_r16_BAG_L1    0.689169   0.729467    f1_macro   
3    ExtraTrees_r197_BAG_L1    0.687728   0.708666    f1_macro   
4     ExtraTrees_r42_BAG_L1    0.672764   0.705213    f1_macro   
5   RandomForestEntr_BAG_L1    0.670982   0.704009    f1_macro   
6     ExtraTrees_r49_BAG_L1    0.670025   0.698599    f1_macro   
7     ExtraTreesEntr_BAG_L1    0.669827   0.699843    f1_macro   
8  RandomForest_r195_BAG_L1    0.669183   0.713571    f1_macro   
9   RandomForestGini_BAG_L1    0.666690   0.701198    f1_macro   

   pred_time_test  pred_time_val    fit_time  pred_time_test_marginal  \
0        5.623425       0.177090  310.831368                 0.018216   
1        1.423129       0.002539   55.940349                 1.423129   
2        0.725390       0.004541    7.771133                 0.725390   
3        0.739420       0.003758    4.498879                 0.739420   
4        0.872644       0.003970    3.222078                 0.872644   
5        1.114933       0.003503    5.659376                 1.114933   
6        0.748843       0.003213    3.493328                 0.748843   
7        0.847131       0.003893    3.475834                 0.847131   
8        0.951284       0.005491    6.863560                 0.951284   
9        2.260559       0.002471    5.661572                 2.260559   

   pred_time_val_marginal  fit_time_marginal  stack_level  can_infer  \
0                0.030227          81.133102            2       True   
1                0.002539          55.940349            1       True   
2                0.004541           7.771133            1       True   
3                0.003758           4.498879            1       True   
4                0.003970           3.222078            1       True   
5                0.003503           5.659376            1       True   
6                0.003213           3.493328            1       True   
7                0.003893           3.475834            1       True   
8                0.005491           6.863560            1       True   
9                0.002471           5.661572            1       True   

   fit_order  
0         76  
1         22  
2         65  
3         63  
4         13  
5          4  
6         37  
7          6  
8         17  
9          3

In [12]:
# For a single specified model: make predictions and perform detailed evaluation on hold out test data
# i = -1  # index of model to use
# model_to_use = automl_predictor.model_names()[i]
model_to_use = automl_std_leaderboard_testdata.iloc[0, 0] # use best model from leaderboard
print(f"Model to be evaluated: {model_to_use}")
preds_y_test = automl_predictor.predict(X_test, model=model_to_use)
print("Predictions:  ", list(preds_y_test)[:5])

print(classification_report(y_test, preds_y_test))

Model to be evaluated: WeightedEnsemble_L2


Predictions:   ['Blister and sealed blist', 'Corrugated carton', 'Plastic bag with header', 'Tube', 'Corrugated carton']


/Users/dat/miniconda3/envs/py_ml_packaging_classification/lib/python3.11/site-packages/sklearn/metrics/_classification.py:1509: UndefinedMetricWarning: Precision is ill-defined and being set to 0.0 in labels with no predicted samples. Use `zero_division` parameter to control this behavior.
  _warn_prf(average, modifier, f"{metric.capitalize()} is", len(result))
/Users/dat/miniconda3/envs/py_ml_packaging_classification/lib/python3.11/site-packages/sklearn/metrics/_classification.py:1509: UndefinedMetricWarning: Precision is ill-defined and being set to 0.0 in labels with no predicted samples. Use `zero_division` parameter to control this behavior.
  _warn_prf(average, modifier, f"{metric.capitalize()} is", len(result))


                            precision    recall  f1-score   support

   Blister and Insert Card       0.87      0.86      0.86      1749
  Blister and sealed blist       0.78      0.84      0.81      1582
            Book packaging       0.00      0.00      0.00         2
Cardb. Sleeve w - w/o Shr.       0.70      0.69      0.69       135
  Cardboard hanger w/o bag       0.94      0.80      0.86        80
    Carton cover (Lid box)       0.53      0.72      0.61       130
   Carton tube with or w/o       1.00      0.89      0.94         9
                      Case       0.80      0.85      0.82        97
         Corrugated carton       0.83      0.77      0.80       774
        Countertop display       0.97      1.00      0.98        30
                  Envelope       0.95      0.93      0.94        59
          Fabric packaging       1.00      0.33      0.50         3
            Folding carton       0.85      0.81      0.83      1644
              Hanger/ Clip       0.93      0.96

/Users/dat/miniconda3/envs/py_ml_packaging_classification/lib/python3.11/site-packages/sklearn/metrics/_classification.py:1509: UndefinedMetricWarning: Precision is ill-defined and being set to 0.0 in labels with no predicted samples. Use `zero_division` parameter to control this behavior.
  _warn_prf(average, modifier, f"{metric.capitalize()} is", len(result))


# AutoML: custom pre-processing; restricted selection of models including HPO and model ensembling

## Define features and target, performe oversampling, split data into train and test

In [13]:
# Define features and target
X = df_sub.iloc[:, :-1]
y = df_sub.iloc[:, -1]  # the last column is the target

In [14]:
distribution_classes = y.value_counts()
print('Class distribution before oversmapling')
print(distribution_classes.to_dict())

# NOTE: Oversampling so each class has at least 100 sample; to properly apply CV and evaluation
dict_oversmapling = {
    'Metal Cassette': 100,
    'Carton tube with or w/o': 100,
    'Wooden box': 100,
    'Fabric packaging': 100,
    'Book packaging': 100
}
# define oversampling strategy
oversampler = RandomOverSampler(sampling_strategy=dict_oversmapling, random_state=SEED)
# fit and apply the transform
X_oversample, y_oversample = oversampler.fit_resample(X, y)

distribution_classes = y_oversample.value_counts()
print('\n')
print('Class distribution after oversmapling')
print(distribution_classes.to_dict())

Class distribution before oversmapling
{'Hanger/ Clip': 13543, 'Tube': 11687, 'Blister and Insert Card': 8744, 'TightPack': 8296, 'Folding carton': 8219, 'Blister and sealed blist': 7912, 'Corrugated carton': 3872, 'Paperboard pouch': 3478, 'Trap Folding Card': 2188, 'Plastic Pouch': 1904, 'Plastic bag with header': 1850, 'Plastic Cassette': 1708, 'Shrink film and insert o': 1499, 'Plastic Box': 1491, 'Unpacked': 1415, 'Skincard': 1143, 'Trap Card': 804, 'Cardb. Sleeve w - w/o Shr.': 676, 'Carton cover (Lid box)': 652, 'Case': 485, 'Tray Packer': 431, 'Cardboard hanger w/o bag': 400, 'Envelope': 295, 'Countertop display': 150, 'Metal Cassette': 50, 'Carton tube with or w/o': 44, 'Wooden box': 16, 'Fabric packaging': 15, 'Book packaging': 10}


Class distribution after oversmapling
{'Hanger/ Clip': 13543, 'Tube': 11687, 'Blister and Insert Card': 8744, 'TightPack': 8296, 'Folding carton': 8219, 'Blister and sealed blist': 7912, 'Corrugated carton': 3872, 'Paperboard pouch': 3478, 'Trap 

In [15]:
# Generate train/test sets
X_train, X_test, y_train, y_test = train_test_split(
    X_oversample, y_oversample, test_size=0.2, stratify=y_oversample,
    random_state=SEED
)

In [16]:
# DEFINE & EXECUTE PIPELINE

# define feature processing pipeline
# define numerical feature processing
numerical_features = X_train.select_dtypes(include='number').columns.tolist()
# print(f'There are {len(numerical_features)} numerical features:', '\n')
# print(numerical_features)
numeric_feature_pipeline = Pipeline(steps=[
    ('impute', SimpleImputer(strategy='median')),
    ('log_transform', PowerTransformer()),
    # ('scale', MinMaxScaler())
])
# define categorical feature processing
categorical_features = X_train.select_dtypes(exclude='number').columns.tolist()
# print(f'There are {len(categorical_features)} categorical features:', '\n')
# print(categorical_features)
categorical_feature_pipeline = Pipeline(steps=[
    ('impute', SimpleImputer(strategy='most_frequent')),
    ('ordinal', OrdinalEncoder(handle_unknown='use_encoded_value', unknown_value=np.nan)),
    # ('one_hot', OneHotEncoder(handle_unknown='ignore', max_categories=None, sparse=False))
])
# apply both pipeline on seperate columns using "ColumnTransformer"
preprocess_pipeline = ColumnTransformer(transformers=[
    ('number', numeric_feature_pipeline, numerical_features),
    ('category', categorical_feature_pipeline, categorical_features)
]).set_output(transform="pandas")
X_train_transformed = preprocess_pipeline.fit_transform(X_train)

# encode target variable
label_encoder = LabelEncoder()
y_train_transformed = label_encoder.fit_transform(y_train)
y_train_transformed = pd.Series(data=y_train_transformed, index=y_train.index, name=y_train.name)

## Transform to AutoML data format

In [17]:
df_train = pd.concat([X_train_transformed, y_train_transformed], axis=1)

In [18]:
train_data = TabularDataset(df_train)
if subsample is True:
    train_data = train_data.sample(n=subsample_size, random_state=SEED)

## AutoML training pipeline

In [19]:
label = 'packaging_category'
automl_predictor = TabularPredictor(
    label=label,
    problem_type='multiclass',
    eval_metric='f1_macro',
    sample_weight='balance_weight'
).fit(
    train_data=train_data,
    tuning_data=None, # If tuning_data = None, fit() will automatically hold out some random validation examples from train_data.
    holdout_frac=0.2, # Default value (if None) is selected based on the number of rows in the training data.
    time_limit=3*60*60,
    presets=['best_quality'], # default = ['medium_quality'], any user-specified arguments in fit() will override the values used by presets.
    # auto_stack=False, # Whether AutoGluon should automatically utilize bagging and multi-layer stack ensembling to boost predictive accuracy.
    # included_model_types=['LR', 'KNN', 'RF', 'XT', 'GBM', 'XGB', 'CAT', 'NN'], 
    # excluded_model_types=['FASTAI', 'AG_AUTOMM'],
    hyperparameter_tune_kwargs = {  # HPO is not performed unless hyperparameter_tune_kwargs is specified. Searchspaces are provided for some models, but not for all. Where no searchspace is provided, a fixed set of hyper-parameters is defined. (see /searchspace under each model: https://github.com/autogluon/autogluon/tree/master/tabular/src/autogluon/tabular/models).
        # 'num_trials': 15, # try at most n different hyperparameter configurations for each type of model
        'scheduler' : 'local',
        'searcher': 'auto', # ‘auto’: Perform bayesian optimization search on NN_TORCH and FASTAI models. Perform random search on other models.
    }  # Refer to TabularPredictor.fit docstring for all valid values
)

No path specified. Models will be saved in: "AutogluonModels/ag-20240403_232939"
Presets specified: ['best_quality']
Stack configuration (auto_stack=True): num_stack_levels=1, num_bag_folds=8, num_bag_sets=1
Dynamic stacking is enabled (dynamic_stacking=True). AutoGluon will try to determine whether the input data is affected by stacked overfitting and enable or disable stacking as a consequence.
Detecting stacked overfitting by sub-fitting AutoGluon on the input data. That is, copies of AutoGluon will be sub-fit on subset(s) of the data. Then, the holdout validation data is used to detect stacked overfitting.
Sub-fit(s) time limit is: 10800 seconds.
Starting holdout-based sub-fit for dynamic stacking. Context path is: AutogluonModels/ag-20240403_232939/ds_sub_fit/sub_fit_ho.
Using predefined sample weighting strategy: balance_weight. Evaluation metrics will ignore sample weights, specify weight_evaluation=True to instead report weighted metrics.
Beginning AutoGluon training ... Time l

In [20]:
# Evaluation of models on training data
automl_predictor.leaderboard()

model  score_val eval_metric  pred_time_val  \
0           WeightedEnsemble_L3   0.812791    f1_macro       0.451915   
1         ExtraTreesGini_BAG_L2   0.810554    f1_macro       0.420358   
2         ExtraTrees_r49_BAG_L2   0.810341    f1_macro       0.420362   
3        ExtraTrees_r126_BAG_L2   0.805897    f1_macro       0.419957   
4         ExtraTreesEntr_BAG_L2   0.804725    f1_macro       0.420267   
..                          ...        ...         ...            ...   
76  NeuralNetFastAI_r187_BAG_L1   0.240252    f1_macro       0.002969   
77          LightGBM_r94_BAG_L1   0.205092    f1_macro       0.003622   
78  NeuralNetFastAI_r100_BAG_L1   0.184068    f1_macro       0.002735   
79   NeuralNetFastAI_r65_BAG_L1   0.157099    f1_macro       0.004012   
80  NeuralNetFastAI_r143_BAG_L1   0.135900    f1_macro       0.005415   

       fit_time  pred_time_val_marginal  fit_time_marginal  stack_level  \
0   2015.554166                0.026504          83.006222            3   
1   1845.275462                0.002725          40.914553            2   
2   1844.834222                0.002729          40.473313            2   
3   1851.160078                0.002324          46.799169            2   
4   1847.388392                0.002634          43.027484            2   
..          ...                     ...                ...          ...   
76    29.297900                0.002969          29.297900            1   
77    31.218024                0.003622          31.218024            1   
78    29.828656                0.002735          29.828656            1   
79    30.883424                0.004012          30.883424            1   
80    29.679920                0.005415          29.679920            1   

    can_infer  fit_order  
0        True         81  
1        True         76  
2        True         78  
3        True         80  
4        True         77  
..        ...        ...  
76       True         71  
77       True         41  
78       True         68  
79       True         45  
80       True         26  

[81 rows x 10 columns]

In [21]:
# Evaluation of models on test data

# process X_test for evaluation and predictions
X_test_transformed = preprocess_pipeline.transform(X_test)

# evaluate models on test data
y_test_transformed = label_encoder.transform(y_test)
y_test_transformed = pd.Series(data=y_test_transformed, index=y_test.index, name=y_test.name)
df_test = pd.concat([X_test_transformed, y_test_transformed], axis=1)
test_data = TabularDataset(df_test)

automl_custom_leaderboard_testdata = automl_predictor.leaderboard(test_data)
automl_custom_leaderboard_testdata.head(10)

/Users/dat/miniconda3/envs/py_ml_packaging_classification/lib/python3.11/site-packages/autogluon/tabular/models/fastainn/tabular_nn_fastai.py:200: FutureWarning: The 'downcast' keyword in fillna is deprecated and will be removed in a future version. Use res.infer_objects(copy=False) to infer non-object dtype, or pd.to_numeric with the 'downcast' keyword to downcast numeric results.
  df = df.fillna(column_fills, inplace=False, downcast=False)
/Users/dat/miniconda3/envs/py_ml_packaging_classification/lib/python3.11/site-packages/autogluon/tabular/models/fastainn/tabular_nn_fastai.py:200: FutureWarning: The 'downcast' keyword in fillna is deprecated and will be removed in a future version. Use res.infer_objects(copy=False) to infer non-object dtype, or pd.to_numeric with the 'downcast' keyword to downcast numeric results.
  df = df.fillna(column_fills, inplace=False, downcast=False)
/Users/dat/miniconda3/envs/py_ml_packaging_classification/lib/python3.11/site-packages/autogluon/tabular/m

model  score_test  score_val eval_metric  \
0       WeightedEnsemble_L3    0.793829   0.812791    f1_macro   
1  RandomForest_r166_BAG_L2    0.782015   0.792096    f1_macro   
2     ExtraTreesEntr_BAG_L2    0.780580   0.804725    f1_macro   
3     ExtraTreesGini_BAG_L2    0.778353   0.810554    f1_macro   
4     ExtraTrees_r49_BAG_L2    0.778249   0.810341    f1_macro   
5       WeightedEnsemble_L2    0.777451   0.788951    f1_macro   
6    ExtraTrees_r126_BAG_L2    0.776890   0.805897    f1_macro   
7    ExtraTrees_r197_BAG_L1    0.759240   0.781434    f1_macro   
8     ExtraTrees_r42_BAG_L1    0.756203   0.778198    f1_macro   
9     ExtraTreesGini_BAG_L1    0.747845   0.775890    f1_macro   

   pred_time_test  pred_time_val     fit_time  pred_time_test_marginal  \
0       45.142357       0.451915  2015.554166                 0.021836   
1       42.866156       0.423063  1829.681633                 0.400174   
2       43.373253       0.420267  1847.388392                 0.907271   
3       43.406238       0.420358  1845.275462                 0.940256   
4       43.296549       0.420362  1844.834222                 0.830567   
5        3.874498       0.144597   284.553359                 0.016897   
6       43.349698       0.419957  1851.160078                 0.883716   
7        0.778896       0.006808     4.447696                 0.778896   
8        0.859650       0.006268     3.888945                 0.859650   
9        0.869199       0.002733     3.064021                 0.869199   

   pred_time_val_marginal  fit_time_marginal  stack_level  can_infer  \
0                0.026504          83.006222            3       True   
1                0.005430          25.320724            2       True   
2                0.002634          43.027484            2       True   
3                0.002725          40.914553            2       True   
4                0.002729          40.473313            2       True   
5                0.028286          76.573429            2       True   
6                0.002324          46.799169            2       True   
7                0.006808           4.447696            1       True   
8                0.006268           3.888945            1       True   
9                0.002733           3.064021            1       True   

   fit_order  
0         81  
1         79  
2         77  
3         76  
4         78  
5         75  
6         80  
7         62  
8         13  
9          5

In [27]:
# For a single specified model: make predictions and perform detailed evaluation on hold out test data
# i = -1  # index of model to use
# model_to_use = automl_predictor.model_names()[i]
model_to_use = automl_custom_leaderboard_testdata.iloc[0, 0] # use best model from leaderboard
print(f"Model to be evaluated: {model_to_use}")
preds_y_test = automl_predictor.predict(X_test_transformed, model=model_to_use)
print("Predictions:  ", list(preds_y_test)[:5])

preds_y_test_inverse = label_encoder.inverse_transform(preds_y_test)

print(classification_report(y_test, preds_y_test_inverse))

Model to be evaluated: WeightedEnsemble_L3


/Users/dat/miniconda3/envs/py_ml_packaging_classification/lib/python3.11/site-packages/autogluon/tabular/models/fastainn/tabular_nn_fastai.py:200: FutureWarning: The 'downcast' keyword in fillna is deprecated and will be removed in a future version. Use res.infer_objects(copy=False) to infer non-object dtype, or pd.to_numeric with the 'downcast' keyword to downcast numeric results.
  df = df.fillna(column_fills, inplace=False, downcast=False)
/Users/dat/miniconda3/envs/py_ml_packaging_classification/lib/python3.11/site-packages/autogluon/tabular/models/fastainn/tabular_nn_fastai.py:200: FutureWarning: The 'downcast' keyword in fillna is deprecated and will be removed in a future version. Use res.infer_objects(copy=False) to infer non-object dtype, or pd.to_numeric with the 'downcast' keyword to downcast numeric results.
  df = df.fillna(column_fills, inplace=False, downcast=False)
/Users/dat/miniconda3/envs/py_ml_packaging_classification/lib/python3.11/site-packages/autogluon/tabular/m

Predictions:   [24, 0, 1, 26, 26]
                            precision    recall  f1-score   support

   Blister and Insert Card       0.79      0.88      0.83      1749
  Blister and sealed blist       0.79      0.81      0.80      1582
            Book packaging       1.00      1.00      1.00        20
Cardb. Sleeve w - w/o Shr.       0.81      0.43      0.56       135
  Cardboard hanger w/o bag       1.00      0.36      0.53        80
    Carton cover (Lid box)       0.69      0.58      0.63       130
   Carton tube with or w/o       0.94      0.80      0.86        20
                      Case       0.44      0.66      0.53        97
         Corrugated carton       0.82      0.76      0.79       774
        Countertop display       0.86      0.80      0.83        30
                  Envelope       0.90      0.90      0.90        59
          Fabric packaging       1.00      1.00      1.00        20
            Folding carton       0.81      0.80      0.80      1644
             